# Boundary Strength

In [ ]:
#Boundary strength

#Packages
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import cooler 
import cooltools.lib.plotting
from cooltools import insulation
import seaborn as sns
import pandas as pd
import cooltools
import coolpuppy
import bbi

from packaging import version
if version.parse(cooltools.__version__) < version.parse('0.5.1'):
    raise AssertionError("tutorials rely on cooltools version 0.5.1 or higher,"+
                         "please check your cooltools version and update to the latest")

#Calculate number of boundaries and boundary strength

main_directory =
resolution_boundary = 80 
sample="INO80"

path_to_cool = 
clr = cooler.Cooler(path_to_cool)
windows = [400, 640, 800] 
insulation_table = insulation(clr, windows, verbose=True)


#Calculate number of boundaries
#It relies on a boundary strength threshold set by Otsu and Li.

from skimage.filters import threshold_li, threshold_otsu

plt.rcParams['font.size'] = 8
histkwargs = dict(
    bins=10**np.linspace(-4,1,200),
    histtype='step',
    lw=1,
)

f, axs = plt.subplots(len(windows), 1, sharex=True, figsize=(3,3), constrained_layout=True)
thresholds_li = {}
thresholds_otsu = {}
for i, (w, ax) in enumerate(zip(windows, axs)):
    ax.hist(
        insulation_table[f'boundary_strength_{w}'],
        **histkwargs
    )
    thresholds_li[w] = threshold_li(insulation_table[f'boundary_strength_{w}'].dropna().values)
    thresholds_otsu[w] = threshold_otsu(insulation_table[f'boundary_strength_{w}'].dropna().values)
    n_boundaries_li = (insulation_table[f'boundary_strength_{w}'].dropna()>=thresholds_li[w]).sum()
    n_boundaries_otsu = (insulation_table[f'boundary_strength_{w}'].dropna()>=thresholds_otsu[w]).sum()
    ax.axvline(thresholds_li[w], c='green')
    ax.axvline(thresholds_otsu[w], c='magenta')
    ax.text(0.01, 0.9,
             f'Window {w}bp',
             ha='left',
             va='top',
             transform=ax.transAxes)
    ax.text(0.01, 0.7,
            f'{n_boundaries_otsu} boundaries (Otsu)',
            c='magenta',
            ha='left',
            va='top',
            transform=ax.transAxes)
    ax.text(0.01, 0.5,
            f'{n_boundaries_li} boundaries (Li)',
            c='green',
            ha='left',
            va='top',
            transform=ax.transAxes)

    ax.set(
        xscale='log',
        ylabel='# boundaries'
    )

axs[-1].set(xlabel='Boundary strength')

#Calculate how many of the boundaries have Reb1 or Abf1 bound?
#Output of Reb1/Abf1 enrichment vs boundary strength


is_boundary = np.any([
        ~insulation_table[f'boundary_strength_{w}'].isnull()
        for w in windows],
    axis=0)
boundaries = insulation_table[is_boundary]




from skimage.filters import threshold_li, threshold_otsu


for file in ['INO80','ISW2','Chd1','RSC','TFs']:
    path_to_Reb1_fc_bw = 
    path_to_Abf1_fc_bw
   
    flank=10
    Reb1_chip_signal = bbi.stackup(
        path_to_Reb1_fc_bw,
        boundaries.chrom,
        boundaries.start-flank,
        boundaries.end+flank,
        bins=1).flatten()

    Abf1_chip_signal = bbi.stackup(
        path_to_Abf1_fc_bw,
        boundaries.chrom,
        boundaries.start-flank,
        boundaries.end+flank,
        bins=1).flatten()

    w=windows[2]
    f, (ax1,ax2) = plt.subplots(1,2, figsize=(7,3))
    plt.subplots_adjust(left=0.1,
                        bottom=0.4,
                        right=0.9,
                        top=0.9,
                        wspace=0.4,
                        hspace=0.4)

    f.suptitle('SGD + GRF + '+sample+'\nChIP data of '+str(file), y=1.05)
    ax1.loglog(
        boundaries[f'boundary_strength_{w}'],
        Reb1_chip_signal,
        'o',
        markersize=0.5,
        alpha=0.5,
        color='indigo'
    );
    ax1.set(
        xlim=(1e-5,1e1),
        ylim=(1e-2,1e4),
        xlabel='Boundary strength',
        ylabel='Reb1 enrichment over input\nin vitro ChIP')

    ax1.axvline(thresholds_li[w], ls='--', color='green', label='Li threshold')


    ax2.loglog(
        boundaries[f'boundary_strength_{w}'],
        Abf1_chip_signal,
        'o',
        markersize=0.5,
        alpha=0.5,
        color='indigo'
    );
    ax2.set(
        xlim=(1e-5,1e1),
        ylim=(1e-2,1e4),
        xlabel='Boundary strength',
        ylabel='Abf1 enrichment over input\nin vitro ChIP')

    ax2.axvline(thresholds_li[w], ls='--', color='green', label='Li threshold')
    f.figure.savefig('sample+'_invitroChIP-'+file+'.pdf', dpi=100, bbox_inches='tight')

#Reb1/Abf1 ChIP strength vs Distance to Boundary

window_size = 2

for grf in ["Reb1","Abf1"]:
    chip_data = 
    top_boundaries = insulation_table[insulation_table[f'boundary_strength_{windows[window_size]}']>=thresholds_li[windows[window_size]]]
    
    flank = 5000 # Length of flank to one side from the boundary, in basepairs
    nbins = 100   # Number of bins to split the region
    resolution = 80

    stackup = bbi.stackup(chip_data,
                        top_boundaries.chrom,
                        top_boundaries.start+resolution//2-flank,
                        top_boundaries.start+resolution//2+flank,
                        bins=nbins)

    f, ax = plt.subplots(figsize=[7,5])
    ax.plot(np.nanmean(stackup, axis=0) )
    ax.set(xticks=np.arange(0, nbins+1, 10),
        xticklabels=(np.arange(0, nbins+1, 10)-nbins//2)*flank*2/nbins,
        xlabel='Distance from boundary, bp',
        ylabel=grf+' in vitro ChIP-Seq mean fold change over input');
    ax.set_yscale("log")
    ax.set_ylim(top=1e3)

    


